In [1]:
# Creates a database, clears if exists and fills with training data
import sqlite3
import codecs
import random

# Connect to database (using sqlite3 lib built into python)
conn = sqlite3.connect( 'comp3208_2.db')

# Read in training data file
readHandle = codecs.open( 'comp3208-train-small.csv', 'r', 'utf-8', errors = 'replace' )
listLines = readHandle.readlines()
readHandle.close()
    
# Creates a table for training data, deletes all data
c = conn.cursor()
c.execute( 'CREATE TABLE IF NOT EXISTS training_table (UserID INT, ItemID INT, Rating FLOAT, Prediction1 FLOAT, Prediction2 FLOAT)' )
conn.commit()
c.execute( 'DELETE FROM training_table' )
conn.commit()
# Inserts data from csv file into training data table (userid, itemid, rating, timestamp - currently not included)
for strLine in listLines :
    if len(strLine.strip()) > 0 :
        listParts = strLine.strip().split(',')
        if len(listParts) == 4 :
            # Insert training set into table with an initial predicted rating of 0
            c.execute( 'INSERT INTO training_table VALUES (?,?,?,?,?)', (listParts[0], listParts[1], listParts[2], random.random() * 5, random.random() * 5) )
        else :
            raise Exception( 'failed to parse csv : ' + repr(listParts) )
conn.commit()
    
# Creates an index of the user ID and item ID
c.execute( 'CREATE INDEX IF NOT EXISTS training_table_index on training_table (UserID, ItemID)' )
conn.commit()

In [2]:
# Inserts testing data into a table in database

# Reads in data
readHandle = codecs.open( 'comp3208-test-small.csv', 'r', 'utf-8', errors = 'replace' )
listLines = readHandle.readlines()
readHandle.close()

# Create and clear table for testing data
c2 = conn.cursor()
c2.execute( 'CREATE TABLE IF NOT EXISTS testing_table (UserID INT, ItemID INT, Rating FLOAT, PredRating FLOAT)' )
conn.commit()
c2.execute( 'DELETE FROM testing_table' )
conn.commit()
# Inserts data from csv file into testing data table (userid, itemid, timestamp - currently not used)
for strLine in listLines :
    if len(strLine.strip()) > 0 :
        listParts = strLine.strip().split(',')
        if len(listParts) == 3 :
            # Insert training set into table with a rating and predicted rating of 0
            c2.execute( 'INSERT INTO testing_table VALUES (?,?,?,?)', (listParts[0], listParts[1], 0, 0) )
        else :
            raise Exception( 'failed to parse csv : ' + repr(listParts) )
conn.commit()

In [3]:
alpha = 0.0003
beta = 0.9
steps = 100
K = 2

c.execute('SELECT COUNT(*) FROM training_table')
N = c.fetchall()[0][0]


sql = 'SELECT * FROM training_table'
c.execute(sql)
#data = c.fetchall()
data2 = []
[data2.append(list(x)) for x in c.fetchall()]

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

In [4]:
from sklearn.model_selection import train_test_split

c.execute('SELECT UserID, ItemID from training_table')
features = []
[features.append([x[0],x[1]]) for x in c.fetchall()]

c.execute('SELECT Rating from training_table')
labels = []
[labels.append(x[0]) for x in c.fetchall()]

x_train, x_test, y_train, y_test = train_test_split(features, labels, test_size=0.33, random_state=42)

In [5]:
preds = []
for i in x_train:
    sql = 'SELECT Prediction1, Prediction2 FROM training_table WHERE UserID = ' + str(i[0]) + ' AND ItemID = ' + str(i[1])
    c.execute(sql)
    [preds.append([x[0],x[1]]) for x in c.fetchall()]

In [14]:
import numpy as np
N = len(x_train)
for step in range(steps):
    for i in range(N):
        sql = 'SELECT Prediction1, Prediction2 FROM training_table WHERE UserID = ' + str(x_train[i][0]) + ' AND ItemID = ' + str(x_train[i][1])
        c.execute(sql)
        pred1, pred2 = c.fetchall()[0]
        #print(pred1, pred2)
        curPred = y_train[i] - np.dot(pred1, pred2)
        pred1 = pred1 + alpha * (2 * curPred * pred2 - beta * pred1)
        pred2 = pred2 + alpha * (2 * curPred * pred1 - beta * pred2)
        sql = 'UPDATE training_table SET Prediction1 = ' + str(pred1) + ', Prediction2 = ' + str(pred2) + ' WHERE UserID = ' + str(x_train[i][0]) + ' AND ItemID = ' + str(x_train[i][1])
        c.execute(sql)
    print(step)
c.commit()

0/6315249
1/6315249
2/6315249
3/6315249
4/6315249
5/6315249
6/6315249
7/6315249
8/6315249
9/6315249
10/6315249
11/6315249
12/6315249
13/6315249
14/6315249
15/6315249
16/6315249
17/6315249
18/6315249
19/6315249
20/6315249
21/6315249
22/6315249
23/6315249
24/6315249
25/6315249
26/6315249
27/6315249
28/6315249
29/6315249
30/6315249
31/6315249
32/6315249
33/6315249
34/6315249
35/6315249
36/6315249
37/6315249
38/6315249
39/6315249
40/6315249
41/6315249
42/6315249
43/6315249
44/6315249
45/6315249
46/6315249
47/6315249
48/6315249
49/6315249
50/6315249
51/6315249
52/6315249
53/6315249
54/6315249
55/6315249
56/6315249
57/6315249
58/6315249
59/6315249
60/6315249
61/6315249
62/6315249
63/6315249
64/6315249
65/6315249
66/6315249
67/6315249
68/6315249
69/6315249
70/6315249
71/6315249
72/6315249
73/6315249
74/6315249
75/6315249
76/6315249
77/6315249
78/6315249
79/6315249
80/6315249
81/6315249
82/6315249
83/6315249
84/6315249
85/6315249
86/6315249
87/6315249
88/6315249
89/6315249
90/6315249
91/631524

954/6315249
955/6315249
956/6315249
957/6315249
958/6315249
959/6315249
960/6315249
961/6315249
962/6315249
963/6315249
964/6315249
965/6315249
966/6315249
967/6315249
968/6315249
969/6315249
970/6315249
971/6315249
972/6315249
973/6315249
974/6315249
975/6315249
976/6315249
977/6315249
978/6315249
979/6315249
980/6315249
981/6315249
982/6315249
983/6315249
984/6315249
985/6315249
986/6315249
987/6315249
988/6315249
989/6315249
990/6315249
991/6315249
992/6315249
993/6315249
994/6315249
995/6315249
996/6315249
997/6315249
998/6315249
999/6315249
1000/6315249
1001/6315249
1002/6315249
1003/6315249
1004/6315249
1005/6315249
1006/6315249
1007/6315249
1008/6315249
1009/6315249
1010/6315249
1011/6315249
1012/6315249
1013/6315249
1014/6315249
1015/6315249
1016/6315249
1017/6315249
1018/6315249
1019/6315249
1020/6315249
1021/6315249
1022/6315249
1023/6315249
1024/6315249
1025/6315249
1026/6315249
1027/6315249
1028/6315249
1029/6315249
1030/6315249
1031/6315249
1032/6315249
1033/6315249
1034/6

1980/6315249
1981/6315249
1982/6315249
1983/6315249
1984/6315249
1985/6315249
1986/6315249
1987/6315249
1988/6315249
1989/6315249
1990/6315249
1991/6315249
1992/6315249
1993/6315249
1994/6315249
1995/6315249
1996/6315249
1997/6315249
1998/6315249
1999/6315249
2000/6315249
2001/6315249
2002/6315249
2003/6315249
2004/6315249
2005/6315249
2006/6315249
2007/6315249
2008/6315249
2009/6315249
2010/6315249
2011/6315249
2012/6315249
2013/6315249
2014/6315249
2015/6315249
2016/6315249
2017/6315249
2018/6315249
2019/6315249
2020/6315249
2021/6315249
2022/6315249
2023/6315249
2024/6315249
2025/6315249
2026/6315249
2027/6315249
2028/6315249
2029/6315249
2030/6315249
2031/6315249
2032/6315249
2033/6315249
2034/6315249
2035/6315249
2036/6315249
2037/6315249
2038/6315249
2039/6315249
2040/6315249
2041/6315249
2042/6315249
2043/6315249
2044/6315249
2045/6315249
2046/6315249
2047/6315249
2048/6315249
2049/6315249
2050/6315249
2051/6315249
2052/6315249
2053/6315249
2054/6315249
2055/6315249
2056/6315249

3043/6315249
3044/6315249
3045/6315249
3046/6315249
3047/6315249
3048/6315249
3049/6315249
3050/6315249
3051/6315249
3052/6315249
3053/6315249
3054/6315249
3055/6315249
3056/6315249
3057/6315249
3058/6315249
3059/6315249
3060/6315249
3061/6315249
3062/6315249
3063/6315249
3064/6315249
3065/6315249
3066/6315249
3067/6315249
3068/6315249
3069/6315249
3070/6315249
3071/6315249
3072/6315249
3073/6315249
3074/6315249
3075/6315249
3076/6315249
3077/6315249
3078/6315249
3079/6315249
3080/6315249
3081/6315249
3082/6315249
3083/6315249
3084/6315249
3085/6315249
3086/6315249
3087/6315249
3088/6315249
3089/6315249
3090/6315249
3091/6315249
3092/6315249
3093/6315249
3094/6315249
3095/6315249
3096/6315249
3097/6315249
3098/6315249
3099/6315249
3100/6315249
3101/6315249
3102/6315249
3103/6315249
3104/6315249
3105/6315249
3106/6315249
3107/6315249
3108/6315249
3109/6315249
3110/6315249
3111/6315249
3112/6315249
3113/6315249
3114/6315249
3115/6315249
3116/6315249
3117/6315249
3118/6315249
3119/6315249

4078/6315249
4079/6315249
4080/6315249
4081/6315249
4082/6315249
4083/6315249
4084/6315249
4085/6315249
4086/6315249
4087/6315249
4088/6315249
4089/6315249
4090/6315249
4091/6315249
4092/6315249
4093/6315249
4094/6315249
4095/6315249
4096/6315249
4097/6315249
4098/6315249
4099/6315249
4100/6315249
4101/6315249
4102/6315249
4103/6315249
4104/6315249
4105/6315249
4106/6315249
4107/6315249
4108/6315249
4109/6315249
4110/6315249
4111/6315249
4112/6315249
4113/6315249
4114/6315249
4115/6315249
4116/6315249
4117/6315249
4118/6315249
4119/6315249
4120/6315249
4121/6315249
4122/6315249
4123/6315249
4124/6315249
4125/6315249
4126/6315249
4127/6315249
4128/6315249
4129/6315249
4130/6315249
4131/6315249
4132/6315249
4133/6315249
4134/6315249
4135/6315249
4136/6315249
4137/6315249
4138/6315249
4139/6315249
4140/6315249
4141/6315249
4142/6315249
4143/6315249
4144/6315249
4145/6315249
4146/6315249
4147/6315249
4148/6315249
4149/6315249
4150/6315249
4151/6315249
4152/6315249
4153/6315249
4154/6315249

...

104583/6315249
104584/6315249
104585/6315249
104586/6315249
104587/6315249
104588/6315249
104589/6315249
104590/6315249
104591/6315249
104592/6315249
104593/6315249
104594/6315249
104595/6315249
104596/6315249
104597/6315249
104598/6315249
104599/6315249
104600/6315249
104601/6315249
104602/6315249
104603/6315249
104604/6315249
104605/6315249
104606/6315249
104607/6315249
104608/6315249
104609/6315249
104610/6315249
104611/6315249
104612/6315249
104613/6315249
104614/6315249
104615/6315249
104616/6315249
104617/6315249
104618/6315249
104619/6315249
104620/6315249
104621/6315249
104622/6315249
104623/6315249
104624/6315249
104625/6315249
104626/6315249
104627/6315249
104628/6315249
104629/6315249
104630/6315249
104631/6315249
104632/6315249
104633/6315249
104634/6315249
104635/6315249
104636/6315249
104637/6315249
104638/6315249
104639/6315249
104640/6315249
104641/6315249
104642/6315249
104643/6315249
104644/6315249
104645/6315249
104646/6315249
104647/6315249
104648/6315249
104649/631

105619/6315249
105620/6315249
105621/6315249
105622/6315249
105623/6315249
105624/6315249
105625/6315249
105626/6315249
105627/6315249
105628/6315249
105629/6315249
105630/6315249
105631/6315249
105632/6315249
105633/6315249
105634/6315249
105635/6315249
105636/6315249
105637/6315249
105638/6315249
105639/6315249
105640/6315249
105641/6315249
105642/6315249
105643/6315249
105644/6315249
105645/6315249
105646/6315249
105647/6315249
105648/6315249
105649/6315249
105650/6315249
105651/6315249
105652/6315249
105653/6315249
105654/6315249
105655/6315249
105656/6315249
105657/6315249
105658/6315249
105659/6315249
105660/6315249
105661/6315249
105662/6315249
105663/6315249
105664/6315249
105665/6315249
105666/6315249
105667/6315249
105668/6315249
105669/6315249
105670/6315249
105671/6315249
105672/6315249
105673/6315249
105674/6315249
105675/6315249
105676/6315249
105677/6315249
105678/6315249
105679/6315249
105680/6315249
105681/6315249
105682/6315249
105683/6315249
105684/6315249
105685/631

106448/6315249
106449/6315249
106450/6315249
106451/6315249
106452/6315249
106453/6315249
106454/6315249
106455/6315249
106456/6315249
106457/6315249
106458/6315249
106459/6315249
106460/6315249
106461/6315249
106462/6315249
106463/6315249
106464/6315249
106465/6315249
106466/6315249
106467/6315249
106468/6315249
106469/6315249
106470/6315249
106471/6315249
106472/6315249
106473/6315249
106474/6315249
106475/6315249
106476/6315249
106477/6315249
106478/6315249
106479/6315249
106480/6315249
106481/6315249
106482/6315249
106483/6315249
106484/6315249
106485/6315249
106486/6315249
106487/6315249
106488/6315249
106489/6315249
106490/6315249
106491/6315249
106492/6315249
106493/6315249
106494/6315249
106495/6315249
106496/6315249
106497/6315249
106498/6315249
106499/6315249
106500/6315249
106501/6315249
106502/6315249
106503/6315249
106504/6315249
106505/6315249
106506/6315249
106507/6315249
106508/6315249
106509/6315249
106510/6315249
106511/6315249
106512/6315249
106513/6315249
106514/631

107410/6315249
107411/6315249
107412/6315249
107413/6315249
107414/6315249
107415/6315249
107416/6315249
107417/6315249
107418/6315249
107419/6315249
107420/6315249
107421/6315249
107422/6315249
107423/6315249
107424/6315249
107425/6315249
107426/6315249
107427/6315249
107428/6315249
107429/6315249
107430/6315249
107431/6315249
107432/6315249
107433/6315249
107434/6315249
107435/6315249
107436/6315249
107437/6315249
107438/6315249
107439/6315249
107440/6315249
107441/6315249
107442/6315249
107443/6315249
107444/6315249
107445/6315249
107446/6315249
107447/6315249
107448/6315249
107449/6315249
107450/6315249
107451/6315249
107452/6315249
107453/6315249
107454/6315249
107455/6315249
107456/6315249
107457/6315249
107458/6315249
107459/6315249
107460/6315249
107461/6315249
107462/6315249
107463/6315249
107464/6315249
107465/6315249
107466/6315249
107467/6315249
107468/6315249
107469/6315249
107470/6315249
107471/6315249
107472/6315249
107473/6315249
107474/6315249
107475/6315249
107476/631

KeyboardInterrupt: 

In [12]:
M = len(x_test)
test_list = []
for i in range(M):
    sql = 'SELECT Prediction1 FROM training_table WHERE UserID = ' + str(x_test[i][0]) + ' AND ItemID != 0'
    c.execute(sql)
    allUserPreds = []
    [allUserPreds.append(x[0]) for x in c.fetchall()]
    avgUser = sum(allUserPreds)/len(allUserPreds)
    #print(avgUser)
    
    sql = 'SELECT Prediction2 FROM training_table WHERE ItemID = ' + str(x_test[i][1])
    c.execute(sql)
    allMoviePreds = []
    [allMoviePreds.append(x[0]) for x in c.fetchall()]
    avgMovie = sum(allMoviePreds)/len(allMoviePreds)
    #print(avgMovie)
    
    #test_list.append( {'user' : x_test[i][0], 'name' : x_test[i][1], 'pred1' : avgUser, 'pred2': avgMovie } )
    #print(i, "/", M)
    sql = 'UPDATE training_table SET Prediction1 = ' + str(avgUser) + ', Prediction2 = ' + str(avgMovie) + ' WHERE UserID = ' + str(x_test[i][0]) + ' AND ItemID = ' + str(x_test[i][1])
    c.execute(sql)
    print(str(i) + "/" + str(M))
c.commit()

0/3110496
1/3110496
2/3110496
3/3110496
4/3110496
5/3110496
6/3110496
7/3110496
8/3110496
9/3110496
10/3110496
11/3110496
12/3110496
13/3110496
14/3110496
15/3110496
16/3110496
17/3110496
18/3110496
19/3110496
20/3110496
21/3110496
22/3110496
23/3110496
24/3110496
25/3110496
26/3110496
27/3110496
28/3110496
29/3110496
30/3110496
31/3110496
32/3110496
33/3110496
34/3110496
35/3110496
36/3110496
37/3110496
38/3110496
39/3110496
40/3110496
41/3110496
42/3110496
43/3110496
44/3110496
45/3110496
46/3110496
47/3110496
48/3110496
49/3110496
50/3110496
51/3110496
52/3110496
53/3110496
54/3110496
55/3110496
56/3110496
57/3110496
58/3110496
59/3110496
60/3110496
61/3110496
62/3110496
63/3110496
64/3110496
65/3110496
66/3110496
67/3110496
68/3110496
69/3110496
70/3110496
71/3110496
72/3110496
73/3110496
74/3110496
75/3110496
76/3110496
77/3110496
78/3110496
79/3110496
80/3110496
81/3110496
82/3110496
83/3110496
84/3110496
85/3110496
86/3110496
87/3110496
88/3110496
89/3110496
90/3110496
91/311049

692/3110496
693/3110496
694/3110496
695/3110496
696/3110496
697/3110496
698/3110496
699/3110496
700/3110496
701/3110496
702/3110496
703/3110496
704/3110496
705/3110496
706/3110496
707/3110496
708/3110496
709/3110496
710/3110496
711/3110496
712/3110496
713/3110496
714/3110496
715/3110496
716/3110496
717/3110496
718/3110496
719/3110496
720/3110496
721/3110496
722/3110496
723/3110496
724/3110496
725/3110496
726/3110496
727/3110496
728/3110496
729/3110496
730/3110496
731/3110496
732/3110496
733/3110496
734/3110496
735/3110496
736/3110496
737/3110496
738/3110496
739/3110496
740/3110496
741/3110496
742/3110496
743/3110496
744/3110496
745/3110496
746/3110496
747/3110496
748/3110496
749/3110496
750/3110496
751/3110496
752/3110496
753/3110496
754/3110496
755/3110496
756/3110496
757/3110496
758/3110496
759/3110496
760/3110496
761/3110496
762/3110496
763/3110496
764/3110496
765/3110496
766/3110496
767/3110496
768/3110496
769/3110496
770/3110496
771/3110496
772/3110496
773/3110496
774/3110496
775/

1346/3110496
1347/3110496
1348/3110496
1349/3110496
1350/3110496
1351/3110496
1352/3110496
1353/3110496
1354/3110496
1355/3110496
1356/3110496
1357/3110496
1358/3110496
1359/3110496
1360/3110496
1361/3110496
1362/3110496
1363/3110496
1364/3110496
1365/3110496
1366/3110496
1367/3110496
1368/3110496
1369/3110496
1370/3110496
1371/3110496
1372/3110496
1373/3110496
1374/3110496
1375/3110496
1376/3110496
1377/3110496
1378/3110496
1379/3110496
1380/3110496
1381/3110496
1382/3110496
1383/3110496
1384/3110496
1385/3110496
1386/3110496
1387/3110496
1388/3110496
1389/3110496
1390/3110496
1391/3110496
1392/3110496
1393/3110496
1394/3110496
1395/3110496
1396/3110496
1397/3110496
1398/3110496
1399/3110496
1400/3110496
1401/3110496
1402/3110496
1403/3110496
1404/3110496
1405/3110496
1406/3110496
1407/3110496
1408/3110496
1409/3110496
1410/3110496
1411/3110496
1412/3110496
1413/3110496
1414/3110496
1415/3110496
1416/3110496
1417/3110496
1418/3110496
1419/3110496
1420/3110496


KeyboardInterrupt: 

In [54]:
sql = 'SELECT Prediction2 FROM training_table WHERE UserID = 1 AND ItemID != 0'
#print(x_test[0][0])
c.execute(sql)
au = []
[au.append(x[0]) for x in c.fetchall()]
av = sum(au)/len(au)
#print(au)
print(av)

sql = 'SELECT Prediction1 FROM training_table WHERE ItemID = 113 AND UserID != 1'
c.execute(sql)
#mu = []
#[mu.append(x[0]) for x in c.fetchall()]
tot = 0
le = 0
for i in c.fetchall():
    tot = tot + i[0]
    le = le + 1
av2 = tot/le
#av2 = sum(mu)/len(mu)
print(av2 * av)

2.3768779219523353
5.949166308292394


In [49]:
sql = 'SELECT * FROM training_table WHERE UserID = ' + str(x_test[0][0]) + ' AND ItemID = ' + str(x_test[0][1])
c.execute(sql)
print(c.fetchall())

[(96695, 11777, 0.0, 2.718278258300538, 2.5180513089052603)]


In [42]:
c.execute( 'INSERT INTO training_table VALUES (?,?,?,?,?)', (test_list['user'], test_list['name'], 0, test_list['pred1'], test_list['pred2']), ' ')

TypeError: list indices must be integers or slices, not str

In [ ]:
import numpy as np
N = len(x_train)
steps = 100
for step in range(steps):
    for i in range(N):
        #print("AAA")
        curPred = y_train[i] - np.dot(preds[i][0], preds[i][1])
        preds[i][0] = preds[i][0] + alpha * (2 * curPred * preds[i][1] - beta * preds[i][0])
        preds[i][1] = preds[i][1] + alpha * (2 * curPred * preds[i][0] - beta * preds[i][1])
    e = 0
    for i in range(N):
        e = e + pow(y_train[i] - (preds[i][0] * preds[i][1]), 2)
        #print(e)
    e = e/N
    print(e)
    if e < 0.0001:
        break

26.457291530715633
25.624416883959057
24.82936384026421
24.069836889353702
23.343717407961396
22.649047090195072
21.984013202663302
21.346935433917157
20.73625414056077


In [ ]:
e = 0
for i in range(M):
    sql = 'SELECT Prediction1, Prediction2 WHERE UserID = ' + str(x_test[i][0]) + ' AND ItemID = ' + str(x_test[i][1])
    c.execute(sql)
    pred1, pred2 = c.fetchall()[0]
    pred = pred1 * pred2
    e = e + pow(y_test[i] - pred, 2)
e = e/M
print(e)

In [ ]:
for i in range(len(preds)):
    sql = 'UPDATE training_table SET Prediction1 = ' + str(preds[i][0]) + ', Prediction2 = ' + str(preds[i][1]) + ' WHERE UserID = ' + str(x_train[i][0]) ' AND ItemID = ' + str(x_train[i][1])
    c.execute(sql)
c.commit()

In [117]:
for i in range(len(data2)):
    if data2[i][0] in x_test:
        data2[i][2] = 0
    print(str(i) + "/" + str(len(data2)))

0/9425745
1/9425745
2/9425745
3/9425745
4/9425745
5/9425745
6/9425745
7/9425745
8/9425745
9/9425745
10/9425745
11/9425745
12/9425745
13/9425745
14/9425745
15/9425745
16/9425745
17/9425745
18/9425745
19/9425745
20/9425745
21/9425745
22/9425745
23/9425745
24/9425745
25/9425745
26/9425745
27/9425745
28/9425745
29/9425745
30/9425745
31/9425745
32/9425745
33/9425745
34/9425745
35/9425745
36/9425745
37/9425745
38/9425745
39/9425745
40/9425745
41/9425745
42/9425745
43/9425745
44/9425745
45/9425745
46/9425745
47/9425745
48/9425745
49/9425745
50/9425745
51/9425745
52/9425745
53/9425745
54/9425745
55/9425745
56/9425745
57/9425745
58/9425745
59/9425745
60/9425745
61/9425745
62/9425745
63/9425745
64/9425745
65/9425745
66/9425745
67/9425745
68/9425745
69/9425745
70/9425745
71/9425745
72/9425745
73/9425745
74/9425745
75/9425745
76/9425745
77/9425745
78/9425745
79/9425745
80/9425745
81/9425745
82/9425745
83/9425745
84/9425745
85/9425745
86/9425745
87/9425745
88/9425745
89/9425745
90/9425745
91/942574

692/9425745
693/9425745
694/9425745
695/9425745
696/9425745
697/9425745
698/9425745
699/9425745
700/9425745
701/9425745
702/9425745
703/9425745
704/9425745
705/9425745
706/9425745
707/9425745
708/9425745
709/9425745
710/9425745
711/9425745
712/9425745
713/9425745
714/9425745
715/9425745
716/9425745
717/9425745
718/9425745
719/9425745
720/9425745
721/9425745
722/9425745
723/9425745
724/9425745
725/9425745
726/9425745
727/9425745
728/9425745
729/9425745
730/9425745
731/9425745
732/9425745
733/9425745
734/9425745
735/9425745
736/9425745
737/9425745
738/9425745
739/9425745
740/9425745
741/9425745
742/9425745
743/9425745
744/9425745
745/9425745
746/9425745
747/9425745
748/9425745
749/9425745
750/9425745
751/9425745
752/9425745
753/9425745
754/9425745
755/9425745
756/9425745
757/9425745
758/9425745
759/9425745
760/9425745
761/9425745
762/9425745
763/9425745
764/9425745
765/9425745
766/9425745
767/9425745
768/9425745
769/9425745
770/9425745
771/9425745
772/9425745
773/9425745
774/9425745
775/

1347/9425745
1348/9425745
1349/9425745
1350/9425745
1351/9425745
1352/9425745
1353/9425745
1354/9425745
1355/9425745
1356/9425745
1357/9425745
1358/9425745
1359/9425745
1360/9425745
1361/9425745
1362/9425745
1363/9425745
1364/9425745
1365/9425745
1366/9425745
1367/9425745
1368/9425745
1369/9425745
1370/9425745
1371/9425745
1372/9425745
1373/9425745


KeyboardInterrupt: 

In [8]:
i=0
for data in x_test:
    i=i+1
    sql = 'UPDATE training_table SET Rating = 0 WHERE UserID = ' + str(data[0]) + ' AND ItemID = ' + str(data[1])
    c.execute(sql)
    #print(str(i) + "/" + str(len(x_test)))
conn.commit()

In [129]:
import numpy as np
for step in range(steps):
    for i in range(N):
        if data2[i][2] != 0:
            curPred = data2[i][2] - np.dot(data2[i][3], data2[i][4])
        data2[i][3] = data2[i][3] + alpha * (2 * curPred * data2[i][4] - beta * data2[i][3])
        data2[i][4] = data2[i][4] + alpha * (2 * curPred * data2[i][3] - beta * data2[i][4])
    e = 0
    for i in range(N):
        if data2[i][2] != 0:
            e = e + pow(data2[i][2] - (data2[i][3] * data2[i][4]), 2)
    e = e/N
    print(e)
    if e < 0.001:
        break

0.3263543141533632
0.24555534675043164
0.18613464059558713
0.14158983218684415
0.10791798474184396
0.08238368804135492
0.06299988238126726
0.04827846005869947
0.037091387748828135
0.02858159545703179
0.022099248587830255
0.01715283147754845
0.01337072030445524
0.01047159559991805
0.008242299433234545
0.006521428159085875


In [137]:
count = 0
e = 0
for i in range(N):
    if data2[i][2] == 0:
        print(str(y_test[count]) + " " + str(data2[i][3] * data2[i][4]))
        e = e + pow(y_test[count] - (data2[i][3] * data2[i][4]), 2)
        count = count+1
    else:
        e = e + pow(data2[i][2] - (data2[i][3] * data2[i][4]), 2)
e = e/N
print(e)

3.5 1.8825702729336158
4.0 0.8798635026787534
4.0 1.1384085278469063
3.0 -6.633742552449837
5.0 -0.12073720122498637
3.0 4.248865876196248
3.0 -15.355176396808313
5.0 10.28080275516481
4.0 1.5840160399692211
4.0 12.451441695028663
4.0 0.21281787872231897
4.5 4.770863569650251
4.0 14.282691846251511
4.5 1.24188247861369
4.5 18.852791960133725
3.0 39.60820740357686
1.5 4.370481768828284
4.0 10.527072372093503
3.5 2.8503267511990216
4.0 0.07915348736565764
3.0 2.775674412642396
4.0 1.8688188188431765
2.5 -4.077977247674292
4.0 0.8397401470879071
5.0 -2.7139047640176615
2.5 5.754453517390548
3.5 0.9827197872689294
2.5 40.31052044924942
4.5 11.533618909664236
5.0 10.753327222073139
3.5 0.5214630482632082
4.0 22.390475726388743
5.0 4.892076361348777
3.0 19.228701212049934
4.0 38.170114589420585
1.5 17.184466570559017
2.0 50.96307413865922
1.0 0.918460461530552
4.0 -0.31646863807316256
5.0 6.314925761490535
5.0 2.7601462079588757
5.0 2.8596745926003577
2.0 24.478535873665404
4.0 1.74367752889

2.0 4.181176637170976
5.0 0.14746600468277266
4.0 -2.31692853688309
3.0 -2.817812031336131
4.0 1.9788438440033713
4.0 2.430323923067012
3.5 0.6109387603609681
3.5 10.163152052031844
3.5 5.303182663781631
4.0 7.911302914308901
4.5 19.815249073632312
1.0 -0.9588508569207932
4.0 3.668495720747657
4.0 2.95707588764411
3.0 5.873215571065847
3.5 4.589173017315039
3.0 3.690367862799544
4.0 3.3089234666461564
4.0 -6.436166439813329
5.0 1.0244383946084423
4.0 19.037174929175343
4.0 108.19699287874445
3.5 73.46917187296404
4.0 170.85439909916124
4.0 5.37945360963667
2.0 4.765900290541119
4.5 11.744677437443858
4.0 2.184425037407298
1.0 0.015250439279981112
4.5 0.35561331614356056
4.5 12.93651575609855
3.5 4.333645131746882
3.0 17.694589603259786
2.5 0.14788659896998632
4.0 -3.670720722002911
1.0 4.176330033859772
5.0 0.30925964108437054
3.5 2.3169132421607412
3.0 -35.482637331626655
2.0 -0.7237205331427977
3.0 -21.574458275150548
2.5 -18.97820633538711
3.0 0.5134527160542541
5.0 1.93297866339288

3.5 8.454121714814226
2.0 19.76515578601554
4.0 23.99123431778963
5.0 4.852148520078233
4.0 8.14016586914776
1.0 0.13544533101932082
3.5 -6.067380528796331
3.5 8.115291192740347
2.0 -0.5210822332866868
3.0 5.093411973756328
3.0 3.223594715078248
4.0 0.758315782685532
1.0 4.28076615718984
4.0 2.3968580709642495
3.0 3.8516015772453893
5.0 5.24861673171609
1.0 2.008357346405941
3.5 0.8556735039173294
0.5 1.0499319164085696
4.0 -18.95814894724568
4.0 -14.68861384121268
4.0 13.231953843291603
3.0 1.6899243428203163
5.0 -0.14043202191068807
4.0 6.886925644859594
3.5 1.129236796742749
3.0 84.79810047127351
4.5 16.310036688560253
4.0 0.9070502202765638
3.5 7.451886236069606
2.5 -0.40575485441782927
4.0 0.02066076616929182
4.0 3.208436212664721
4.0 7.881037700280028
3.5 12.246137149978697
1.0 2.423211217013136
5.0 -0.592976714382122
5.0 6.335739059961326
3.0 7.302553607493841
5.0 1.965100700310499
2.0 0.40888968214179305
4.0 2.8097234177444923
2.0 1.8009690438654749
3.0 0.3955845245017745
4.0 6

3.0 24.683968921543894
2.0 12.236540136311039
1.5 -0.9908644610435101
5.0 3.525563107310633
3.0 -2.635647355080676
4.0 38.48497500234563
3.0 1.7421661231019812
5.0 24.31576834597841
5.0 14.762515562514988
4.0 0.5690556911440878
5.0 3.0712697421494006
3.0 -3.00539282449293
4.0 21.92350406562895
1.0 16.700535779794
3.0 2.874697392277594
4.0 -1.6669902523617848
3.0 12.419500195180847
3.0 4.397817660168168
4.0 0.6708960896944626
4.0 2.492647966876878
3.5 17.939939823654782
5.0 3.8584520423287163
3.5 26.75629936440305
2.5 17.955696208723207
5.0 15.532904738357207
1.0 4.840578468691058
4.0 -7.3227632764097565
4.0 7.24937220806523
4.5 -4.219343953701432
5.0 0.6081312956010143
2.5 6.795600322671273
4.5 0.018894170279019237
3.0 5.193389041902932
5.0 45.93472441257155
3.5 73.90323912212824
3.5 6.661237849002562
3.5 9.825053423084029
3.0 15.421741131617708
4.5 9.470896191817431
3.0 -1.189631936571307
3.0 0.3491559213063877
5.0 12.136142573304037
3.0 9.549006018364743
4.0 -1.0096193362076507
3.5 4

4.0 6.894298850167002
4.0 2.8233996006378543
4.0 69.51833933224937
3.0 4.974429791472837
5.0 5.3210709596902115
5.0 -1.165572128428479
1.0 0.022118757281956846
4.0 2.05068308261683
4.0 4.906399348222447
4.0 1.453100681330862
4.5 13.144160048339433
4.0 5.676569460429979
2.5 0.994597039796677
4.0 -0.18302110839005473
4.0 14.160765188501431
4.5 5.7397896282030345
3.5 8.756849648289148
4.0 -5.789309890454068
3.0 50.228974283796646
1.0 1.3485644437795985
4.0 6.1538835255776005
0.5 38.909543281569874
3.5 11.85700272563233
3.0 0.00790393346561568
3.0 2.5885975240062153
3.5 1.0015527805156468
3.5 8.858017254468537
3.5 2.87857515100548
2.0 -10.449255413311231
4.0 12.430798388692262
4.0 -0.043757338577473
4.0 -0.5997430297879845
3.0 25.331660822089287
3.5 7.392034759057198
3.5 160.00018841273888
3.0 5.785392945961665
4.5 7.737336281999872
3.0 4.330538520132452
4.0 10.72721826692115
4.0 10.739583622507409
4.5 -0.03500083875490334
3.0 1.099010558933201
3.0 2.6774510569568704
4.0 10.420036979204989

...

4.0 7.114655578029949
3.0 -1.872189231395637
3.0 -0.18437761790180868
5.0 11.164768527767874
5.0 1.803230094679142
4.0 6.96477862211617
0.5 0.520245358033968
2.5 5.7380161272426475
5.0 7.263537693991723
4.0 18.148436754940402
4.0 3.416046441645227
5.0 -1.7362033015782214
4.0 -16.801106312850955
2.5 55.49590851634736
3.5 8.410639951207049
2.0 2.4805479341148238
4.5 14.160343472769684
3.0 6.851920763669859
4.5 17.788217334093037
4.5 2.894553825670196
2.5 7.816701632311719
4.0 0.017991176132603683
3.0 2.809097495744977
4.0 44.894236057499135
5.0 25.644612389209282
4.5 1.9917909629352455
4.0 -1.5751925403983897
5.0 -2.2915653881432076
3.0 13.127740606321758
3.0 -0.6546464821555581
3.5 3.547653790377585
3.0 3.4985569876588127
4.5 3.2607509047204597
3.0 5.20771793416129
1.5 3.76843670890717
5.0 -2.2768930499150786
3.0 -1.008922595891541
4.5 4.034203286956964
4.0 1.2374710845863437
4.5 2.1741161547091545
1.0 9.07653527471406
5.0 60.27052325187772
2.5 1.6250058400127843
3.0 2.0561103347288663


3.0 -7.929219985961291
3.5 16.964826823024044
0.5 -16.995882310070936
4.0 -15.046066329722201
0.5 2.6257107210106767
4.0 0.06932103204690239
5.0 -0.8651754478689127
4.5 15.639574839622258
3.0 -3.0872621794375306
4.0 0.013500448062667767
0.5 -3.393897968377256
3.0 1.1753191300243533
2.0 7.237758780441272
2.5 11.04170536932583
2.0 -18.19389958004652
3.0 1.7750910922901382
3.0 8.676549225745243
4.0 12.01108112067731
3.0 2.466722863578832
3.0 6.572923958284004
1.0 12.372315936036701
3.5 -0.4876177990327582
2.0 -21.64088637886964
3.0 -2.2748004481428086
4.0 0.12685011368995547
4.0 -8.273985414486301
4.0 0.6685874967795868
3.0 3.544695208751208
3.5 9.335070340175406
3.0 8.864454574468219
4.5 -1.2812007323826826
1.5 6.001543089800155
2.0 -0.22618834073476296
4.0 0.4948019375865968
1.5 2.357639733211826
5.0 6.769201999863658
5.0 -5.28444041348678
2.5 -3.61677407475782
2.5 0.6731347756417907
4.0 6.316995039921951
5.0 5.5610015713933825
3.5 0.9506877936069282
4.0 40.61934528110154
4.5 15.9273283

3.0 21.66981761078101
1.0 0.0720141728667985
3.0 5.874039349982928
4.0 16.843783175582658
5.0 5.615169017172175
2.5 41.913403754403184
4.0 5.866647393111876
3.0 35.04549891372416
3.0 3.5689493517270017
4.0 0.4813853188046698
3.0 135.11649263873812
4.5 0.32164992689162275
4.0 0.11897929264653503
4.0 14.038590052799345
3.0 30.932059456332528
3.5 18.813775665865293
4.0 1.1713577591390705
3.0 1.2590723866870905
3.5 10.822071118325104
4.0 -7.422221296094609
4.0 0.5647673617347652
4.0 2.122853127700054
5.0 6.461563335844721
3.0 0.06700663599135233
4.5 -8.739587519150234
4.0 5.908942474147354
3.0 3.010525060040307
4.5 4.060643261668711
1.0 1.4328647910042602
3.0 20.63068156114215
4.0 23.949965221716106
5.0 3.2546178700952066
3.5 1.7278906227511504
4.0 34.539800624197994
5.0 115.41693464478513
5.0 1.9214433002641227
4.5 0.7191986584247821
5.0 35.7780995266161
4.5 65.84323688478246
4.0 49.07670790711979
4.5 5.113520010051365
4.5 18.519363684266377
4.0 0.27983341036323645
4.0 3.516544588219448
3

2.5 -13.051985615058179
5.0 5.0748794235836385
2.5 0.5491160846644139
5.0 1.9412875656919617
5.0 6.8306696219484895
4.0 23.079353579832514
4.0 9.394661308523956
4.0 7.017297612530648
3.5 10.063102160032514
5.0 -4.894365534434398
5.0 1.4471491681249589
4.0 14.207203055230112
3.0 5.95028388420422
4.0 3.1780922493513075
2.5 0.3417851871405403
5.0 0.3223008917835718
4.0 9.052132115845655
4.0 7.718172127531736
4.0 -0.0993539304792558
2.5 5.594876596878146
2.0 4.313696242236824
0.5 -0.29664334340192333
4.5 -0.5228613607880609
2.0 3.540791336702819
4.5 2.2210245043118606
3.0 16.010149979716072
2.5 -4.641715866545134
4.0 1.861263471033683
5.0 6.354858473432742
3.5 -4.034546549665418
1.0 1.8676624215636706
1.5 7.658342406608137
3.0 25.48885735378992
2.5 1.7936192298591993
3.0 -0.35845491133429946
4.5 -0.4521354951438101
4.5 2.072837623925629
4.0 -0.09896089336253401
4.5 0.8891993122477972
4.0 1.9307212840264034
4.0 12.536520426737251
4.5 -0.0013149382766444943
5.0 10.383447241837782
2.0 17.8546

KeyboardInterrupt: 

In [6]:
# BACKUP
import numpy as np
for step in range(steps):
    for i in range(N):
        #curPred = data2[i][2] - np.dot(data2[i][3], data2[i][4])
        curPred = data2[i][2] - np.dot(data2[i][3], data2[i][4])
        #curPred = data2[i][2] - data2[i][3] * data2[i][4]
        data2[i][3] = data2[i][3] + alpha * (2 * curPred * data2[i][4] - beta * data2[i][3])
        data2[i][4] = data2[i][4] + alpha * (2 * curPred * data2[i][3] - beta * data2[i][4])

    #eR = data2[i][3] * data2[i][4]
    e = 0
    for i in range(N):
        #e = e + pow(data2[i][2] - (data2[i][3] * data2[i][4]), 2)
        #e = e + (beta/2) * (pow(data2[i][3],2) + pow(data2[i][4],2))
        e = e + pow(data2[i][2] - (data2[i][3] * data2[i][4]), 2)
    e = e/N
    print(e)
    if e < 0.001:
        break

3.0498856947217265
1.5328206451593467
0.9873789222168101
0.6997351396908268
0.5163814331765341
0.3880011892815641
0.29393084169422684
0.22351494161574872
0.17030720835827035
0.12995392805437886
0.09931408194280297
0.07604254328919008
0.0583619517951845
0.04491970371833041
0.03468799190184176
0.0268879410284453


In [12]:
predictions = []
for i in range(len(data2)):
    predictions.append(round(data2[i][3] * data2[i][4] * 2)/2)
    print(str(predictions[i]) + " " + str(data2[i][2]))

4.0 4.0
1.5 1.5
3.0 3.0
4.5 4.5
3.5 3.5
4.0 4.0
4.5 4.5
2.5 2.5
3.0 3.0
4.5 4.5
3.0 3.0
2.0 2.0
3.5 3.5
4.0 4.0
5.0 5.0
3.5 3.5
2.5 2.5
2.5 2.5
4.0 4.0
4.5 4.5
5.0 5.0
4.0 4.0
4.0 4.0
4.5 4.5
4.5 4.5
4.5 4.5
5.0 5.0
4.0 4.0
5.0 5.0
4.0 4.0
5.0 5.0
4.5 4.5
4.0 4.0
4.0 4.0
3.5 3.5
4.5 4.5
4.0 4.0
4.0 4.0
3.0 3.0
5.0 5.0
4.0 4.0
5.0 5.0
4.0 4.0
5.0 5.0
5.0 5.0
5.0 5.0
4.0 4.0
4.0 4.0
5.0 5.0
4.0 4.0
5.0 5.0
4.0 4.0
4.0 4.0
3.0 3.0
3.0 3.0
4.0 4.0
5.0 5.0
5.0 5.0
3.0 3.0
4.0 4.0
4.0 4.0
4.0 4.0
5.0 5.0
4.0 4.0
3.0 3.0
3.0 3.0
5.0 5.0
5.0 5.0
5.0 5.0
4.0 4.0
4.0 4.0
4.0 4.0
3.0 3.0
4.0 4.0
4.0 4.0
4.0 4.0
5.0 5.0
5.0 5.0
4.0 4.0
4.0 4.0
5.0 5.0
4.0 4.0
5.0 5.0
4.0 4.0
4.0 4.0
5.0 5.0
5.0 5.0
4.0 4.0
5.0 5.0
4.0 4.0
5.0 5.0
4.0 4.0
4.0 4.0
4.0 4.0
4.0 4.0
4.0 4.0
4.0 4.0
5.0 5.0
3.0 3.0
4.0 4.0
5.0 5.0
4.0 4.0
3.0 3.0
5.0 5.0
4.0 4.0
5.0 5.0
4.0 4.0
4.0 4.0
3.0 3.0
1.0 1.0
4.0 4.0
5.0 5.0
4.0 4.0
4.0 4.0
3.0 3.0
4.0 4.0
4.0 4.0
4.0 4.0
4.0 4.0
4.0 4.0
4.0 4.0
4.0 4.0
4.0 4.0
4.0 4.0
5.0 5.0


2.0 2.0
4.5 4.5
5.0 5.0
1.5 1.5
2.5 2.5
2.0 2.0
5.0 5.0
3.5 3.5
3.5 3.5
5.0 5.0
3.0 3.0
2.5 2.5
4.5 4.5
2.0 2.0
3.5 3.5
2.0 2.0
3.5 3.5
2.0 2.0
2.5 2.5
3.5 3.5
3.5 3.5
2.0 2.0
1.0 1.0
4.0 4.0
3.0 3.0
3.0 3.0
4.0 4.0
4.0 4.0
2.5 2.5
2.5 2.5
4.5 4.5
4.0 4.0
1.0 1.0
5.0 5.0
3.5 3.5
4.0 4.0
5.0 5.0
3.5 3.5
4.0 4.0
3.0 3.0
2.5 2.5
3.5 3.5
3.5 3.5
2.0 2.0
2.0 2.0
4.5 4.5
3.0 3.0
2.5 2.5
4.0 4.0
3.0 3.0
2.0 2.0
3.5 3.5
1.5 1.5
3.5 3.5
3.5 3.5
2.0 2.0
1.5 1.5
3.5 3.5
2.0 2.0
2.0 2.0
3.0 3.0
3.0 3.0
3.5 3.5
4.5 4.5
4.0 4.0
4.5 4.5
3.0 3.0
3.0 3.0
4.0 4.0
3.0 3.0
2.5 2.5
3.0 3.0
3.5 3.5
3.0 3.0
4.0 4.0
3.0 3.0
4.0 4.0
4.5 4.5
4.0 4.0
3.0 3.0
1.5 1.5
2.5 2.5
4.0 4.0
4.5 4.5
3.0 3.0
4.5 4.5
3.0 3.0
3.0 3.0
3.5 3.5
5.0 5.0
3.5 3.5
3.5 3.5
3.5 3.5
4.0 4.0
4.0 4.0
4.5 4.5
2.0 2.0
4.0 4.0
3.0 3.0
3.0 3.0
3.5 3.5
4.5 4.5
4.0 4.0
3.0 3.0
2.0 2.0
3.0 3.0
3.0 3.0
3.0 3.0
3.5 3.5
4.0 4.0
3.5 3.5
3.0 3.0
4.0 4.0
3.5 3.5
4.0 4.0
4.5 4.5
3.0 3.0
3.5 3.5
4.0 4.0
3.5 3.5
2.5 2.5
4.0 4.0
4.5 4.5
3.5 3.5
4.0 4.0


4.0 4.0
4.0 4.0
5.0 5.0
5.0 5.0
3.5 3.5
2.5 2.5
3.5 3.5
3.5 3.5
4.0 4.0
5.0 5.0
1.0 1.0
4.0 4.0
4.5 4.5
3.5 3.5
4.5 4.5
2.5 2.5
4.0 4.0
3.5 3.5
3.5 3.5
4.5 4.5
4.0 4.0
4.0 4.0
4.5 4.5
2.5 2.5
3.5 3.5
4.0 4.0
3.5 3.5
3.5 3.5
4.5 4.5
4.5 4.5
4.5 4.5
4.0 4.0
3.5 3.5
3.5 3.5
4.0 4.0
5.0 5.0
3.0 3.0
4.0 4.0
4.5 4.5
4.5 4.5
4.5 4.5
4.0 4.0
3.0 3.0
3.0 3.0
3.0 3.0
3.0 3.0
4.0 4.0
4.0 4.0
4.0 4.0
5.0 5.0
3.0 3.0
4.0 4.0
4.0 4.0
5.0 5.0
4.0 4.0
1.0 1.0
2.0 2.0
5.0 5.0
5.0 5.0
4.0 4.0
4.0 4.0
3.0 3.0
3.0 3.0
3.0 3.0
2.0 2.0
4.0 4.0
2.0 2.0
1.0 1.0
3.0 3.0
2.0 2.0
4.0 4.0
2.0 2.0
1.0 1.0
0.5 1.0
3.0 3.0
4.0 4.0
5.0 5.0
2.0 2.0
3.0 3.0
4.0 4.0
1.0 1.0
2.0 2.0
3.0 3.0
4.0 4.0
1.5 1.5
5.0 5.0
4.0 4.0
1.5 1.5
4.5 4.5
3.0 3.0
1.0 1.0
5.0 5.0
5.0 5.0
1.0 1.0
4.5 4.5
4.0 4.0
4.0 4.0
5.0 5.0
3.0 3.0
2.0 2.0
2.0 2.0
2.5 2.5
3.5 3.5
4.0 4.0
3.0 3.0
3.0 3.0
4.0 4.0
2.0 2.0
3.0 3.0
4.0 4.0
3.0 3.0
4.0 4.0
3.0 3.0
3.0 3.0
5.0 5.0
3.0 3.0
4.5 4.5
3.0 3.0
3.0 3.0
5.0 5.0
4.0 4.0
4.5 4.5
4.0 4.0
4.0 4.0
4.0 4.0


4.0 4.0
1.0 1.0
4.0 4.0
2.0 2.0
1.0 1.0
2.0 2.0
3.0 3.0
4.0 4.0
5.0 5.0
2.0 2.0
2.0 2.0
2.0 2.0
3.0 3.0
3.0 3.0
3.0 3.0
1.0 1.0
3.0 3.0
2.0 2.0
4.0 4.0
5.0 5.0
2.0 2.0
2.0 2.0
4.0 4.0
3.0 3.0
5.0 5.0
4.0 4.0
2.0 2.0
3.0 3.0
4.0 4.0
2.0 2.0
2.0 2.0
4.0 4.0
2.0 2.0
3.0 3.0
2.0 2.0
1.0 1.0
5.0 5.0
3.0 3.0
5.0 5.0
2.0 2.0
1.0 1.0
1.0 1.0
3.0 3.0
2.0 2.0
1.0 1.0
3.0 3.0
3.0 3.0
3.0 3.0
2.0 2.0
2.0 2.0
2.0 2.0
2.0 2.0
3.0 3.0
4.0 4.0
3.0 3.0
3.0 3.0
3.0 3.0
2.0 2.0
3.0 3.0
3.0 3.0
4.0 4.0
5.0 5.0
3.0 3.0
3.0 3.0
4.0 4.0
5.0 5.0
4.0 4.0
1.0 1.0
5.0 5.0
5.0 5.0
5.0 5.0
5.0 5.0
5.0 5.0
3.0 3.0
1.5 1.5
5.0 5.0
2.0 2.0
2.0 2.0
3.5 3.5
3.0 3.0
3.0 3.0
2.5 2.5
5.0 5.0
3.0 3.0
2.5 2.5
3.5 3.5
5.0 5.0
4.0 4.0
3.5 3.5
3.5 3.5
4.5 4.5
3.5 3.5
3.5 3.5
3.5 3.5
3.5 3.5
5.0 5.0
4.5 4.5
4.0 4.0
4.0 4.0
4.0 4.0
4.0 4.0
3.5 3.5
4.0 4.0
3.0 3.0
3.0 3.0
4.0 4.0
3.5 3.5
4.0 4.0
4.0 4.0
3.5 3.5
4.0 4.0
4.5 4.5
5.0 5.0
3.5 3.5
4.0 4.0
4.5 4.5
3.5 3.5
3.5 3.5
4.0 4.0
4.0 4.0
3.5 3.5
3.5 3.5
4.0 4.0
3.5 3.5
4.0 4.0


3.0 3.0
3.0 3.0
3.0 3.0
3.0 3.0
4.0 4.0
4.5 4.5
5.0 5.0
3.0 3.0
3.0 3.0
3.0 3.0
4.0 4.0
3.0 3.0
4.0 4.0
4.0 4.0
4.0 4.0
2.0 2.0
4.0 4.0
3.0 3.0
4.0 4.0
4.0 4.0
3.5 3.5
3.5 3.5
3.5 3.5
3.5 3.5
3.5 3.5
1.5 1.5
1.5 1.5
2.0 2.0
2.5 2.5
3.0 3.0
4.0 4.0
5.0 5.0
4.0 4.0
2.0 2.0
4.0 4.0
2.0 2.0
5.0 5.0
4.0 4.0
4.0 4.0
4.0 4.0
5.0 5.0
5.0 5.0
3.0 3.0
5.0 5.0
5.0 5.0
5.0 5.0
3.0 3.0
4.0 4.0
5.0 5.0
4.0 4.0
3.0 3.0
4.0 4.0
4.0 4.0
3.0 3.0
3.0 3.0
4.0 4.0
5.0 5.0
4.0 4.0
5.0 5.0
5.0 5.0
5.0 5.0
4.0 4.0
3.0 3.0
4.0 4.0
3.0 3.0
4.0 4.0
4.0 4.0
3.0 3.0
5.0 5.0
5.0 5.0
3.0 3.0
2.0 2.0
4.0 4.0
4.0 4.0
3.0 3.0
4.0 4.0
4.0 4.0
4.0 4.0
5.0 5.0
4.0 4.0
5.0 5.0
5.0 5.0
3.0 3.0
5.0 5.0
4.0 4.0
2.0 2.0
4.0 4.0
4.0 4.0
5.0 5.0
4.0 4.0
5.0 5.0
5.0 5.0
4.0 4.0
4.0 4.0
5.0 5.0
4.0 4.0
4.0 4.0
4.0 4.0
2.0 2.0
4.0 4.0
5.0 5.0
5.0 5.0
4.0 4.0
5.0 5.0
4.0 4.0
1.5 1.5
0.5 0.5
1.0 1.0
3.5 3.5
3.5 3.5
3.5 3.5
3.0 3.0
4.5 4.5
5.0 5.0
5.0 5.0
3.0 3.0
0.5 0.5
4.0 4.0
0.5 0.5
4.0 4.0
4.0 4.0
4.0 4.0
5.0 5.0
2.0 2.0
4.0 4.0


...

3.0 3.0
2.0 2.0
5.0 5.0
5.0 5.0
4.0 4.0
5.0 5.0
5.0 5.0
5.0 5.0
5.0 5.0
3.0 3.0
4.0 4.0
5.0 5.0
5.0 5.0
3.5 3.5
2.0 2.0
1.0 1.0
3.0 3.0
4.0 4.0
4.5 4.5
5.0 5.0
5.0 5.0
4.0 4.0
3.5 3.5
0.5 0.5
4.0 4.0
4.0 4.0
5.0 5.0
4.0 4.0
5.0 5.0
4.0 4.0
3.5 3.5
3.5 3.5
3.5 3.5
4.0 4.0
3.0 3.0
3.0 3.0
0.5 0.5
3.0 3.0
4.0 4.0
3.0 3.0
0.5 0.5
1.5 1.5
3.5 3.5
0.5 0.5
0.5 0.5
1.5 1.5
3.0 3.0
0.5 0.5
5.0 5.0
3.5 3.5
3.5 3.5
0.5 0.5
4.0 4.0
3.5 3.5
2.5 2.5
4.5 4.5
4.5 4.5
4.5 4.5
4.5 4.5
4.5 4.5
3.5 3.5
2.0 2.0
3.5 3.5
3.0 3.0
2.5 2.5
5.0 5.0
5.0 5.0
5.0 5.0
5.0 5.0
4.0 4.0
5.0 5.0
5.0 5.0
5.0 5.0
4.0 4.0
3.5 3.5
5.0 5.0
5.0 5.0
3.5 3.5
5.0 5.0
5.0 5.0
4.0 4.0
3.5 3.5
4.5 4.5
3.0 3.0
4.0 4.0
3.5 3.5
4.0 4.0
4.5 4.5
5.0 5.0
4.0 4.0
4.5 4.5
4.5 4.5
4.0 4.0
4.5 4.5
3.0 3.0
3.5 3.5
1.0 1.0
4.0 4.0
3.5 3.5
4.5 4.5
4.5 4.5
2.0 2.0
0.5 0.5
2.5 2.5
5.0 5.0
0.5 0.5
3.5 3.5
4.0 4.0
3.5 3.5
3.0 3.0
1.0 1.0
2.5 2.5
4.5 4.5
4.0 4.0
3.5 3.5
3.0 3.0
4.5 4.5
3.5 3.5
1.0 1.0
4.0 4.0
2.5 2.5
4.0 4.0
4.5 4.5
5.0 5.0
5.0 5.0


4.0 4.0
3.0 3.0
4.0 4.0
2.0 2.0
4.0 4.0
4.0 4.0
5.0 5.0
3.0 3.0
3.0 3.0
1.5 1.5
2.0 2.0
2.0 2.0
1.5 1.5
3.0 3.0
3.5 3.5
5.0 5.0
4.0 4.0
3.0 3.0
4.0 4.0
3.5 3.5
3.5 3.5
4.5 4.5
2.5 2.5
0.5 0.5
3.0 3.0
4.0 4.0
4.0 4.0
5.0 5.0
5.0 5.0
5.0 5.0
5.0 5.0
5.0 5.0
5.0 5.0
5.0 5.0
5.0 5.0
5.0 5.0
5.0 5.0
4.0 4.0
4.0 4.0
3.0 3.0
3.0 3.0
5.0 5.0
4.0 4.0
3.0 3.0
4.0 4.0
3.0 3.0
4.0 4.0
4.0 4.0
1.0 1.0
4.0 4.0
4.0 4.0
5.0 5.0
4.0 4.0
4.5 4.5
4.5 4.5
4.0 4.0
4.5 4.5
4.0 4.0
4.0 4.0
4.5 4.5
4.5 4.5
4.0 4.0
4.0 4.0
4.0 4.0
4.5 4.5
3.0 3.0
4.0 4.0
3.5 3.5
4.0 4.0
4.5 4.5
3.5 3.5
4.5 4.5
3.0 3.0
3.5 3.5
5.0 5.0
4.5 4.5
3.0 3.0
4.0 4.0
3.5 3.5
4.0 4.0
4.0 4.0
4.5 4.5
4.0 4.0
5.0 5.0
3.5 3.5
3.5 3.5
4.0 4.0
4.0 4.0
3.0 3.0
3.5 3.5
4.0 4.0
3.5 3.5
4.0 4.0
4.0 4.0
4.0 4.0
4.5 4.5
4.0 4.0
5.0 5.0
4.0 4.0
4.0 4.0
4.5 4.5
4.5 4.5
4.0 4.0
4.0 4.0
4.0 4.0
4.5 4.5
4.5 4.5
4.0 4.0
4.0 4.0
3.5 3.5
4.5 4.5
5.0 5.0
4.5 4.5
4.0 4.0
4.0 4.0
4.5 4.5
3.5 3.5
4.0 4.0
3.5 3.5
4.0 4.0
4.0 4.0
4.0 4.0
3.5 3.5
3.0 3.0
4.5 4.5


3.0 3.0
2.0 2.0
2.0 2.0
4.0 4.0
1.0 1.0
3.0 3.0
2.0 2.0
2.0 2.0
2.0 2.0
4.0 4.0
1.0 1.0
1.0 1.0
4.0 4.0
2.0 2.0
2.0 2.0
3.0 3.0
3.0 3.0
4.0 4.0
2.0 2.0
4.0 4.0
5.0 5.0
3.0 3.0
3.0 3.0
2.0 2.0
4.0 4.0
3.0 3.0
4.0 4.0
4.0 4.0
4.0 4.0
4.0 4.0
5.0 5.0
5.0 5.0
3.0 3.0
5.0 5.0
4.0 4.0
4.0 4.0
4.0 4.0
4.0 4.0
3.0 3.0
3.0 3.0
4.0 4.0
2.0 2.0
4.0 4.0
4.0 4.0
3.0 3.0
5.0 5.0
3.0 3.0
4.0 4.0
2.0 2.0
3.0 3.0
4.0 4.0
3.0 3.0
2.0 2.0
4.0 4.0
3.0 3.0
4.0 4.0
3.0 3.0
4.0 4.0
2.0 2.0
2.0 2.0
3.0 3.0
1.0 1.0
2.0 2.0
3.0 3.0
2.0 2.0
3.0 3.0
4.0 4.0
4.0 4.0
2.0 2.0
4.0 4.0
2.0 2.0
3.0 3.0
3.0 3.0
4.0 4.0
4.0 4.0
4.0 4.0
3.0 3.0
2.0 2.0
5.0 5.0
3.0 3.0
3.0 3.0
4.0 4.0
2.0 2.0
3.0 3.0
3.0 3.0
3.0 3.0
3.0 3.0
2.0 2.0
2.0 2.0
2.0 2.0
2.0 2.0
4.0 4.0
2.0 2.0
3.0 3.0
4.0 4.0
2.0 2.0
5.0 5.0
3.0 3.0
2.0 2.0
3.0 3.0
2.0 2.0
2.0 2.0
3.0 3.0
5.0 5.0
2.0 2.0
3.0 3.0
4.0 4.0
4.0 4.0
2.0 2.0
2.0 2.0
4.0 4.0
3.0 3.0
3.0 3.0
1.0 1.0
3.0 3.0
4.0 4.0
2.0 2.0
4.0 4.0
2.0 2.0
2.0 2.0
2.0 2.0
1.0 1.0
3.0 3.0
2.0 2.0
3.0 3.0


3.5 3.5
2.0 2.0
3.5 3.5
3.5 3.5
3.5 3.5
3.0 3.0
3.0 3.0
3.5 3.5
3.0 3.0
3.0 3.0
2.0 2.0
4.0 4.0
2.0 2.0
1.5 1.5
3.5 3.5
2.5 2.5
1.0 1.0
4.5 4.5
2.5 2.5
3.0 3.0
2.5 2.5
3.5 3.5
3.0 3.0
4.0 4.0
3.5 3.5
2.5 2.5
3.5 3.5
2.5 2.5
3.0 3.0
4.0 4.0
3.5 3.5
4.0 4.0
4.0 4.0
3.0 3.0
3.5 3.5
3.5 3.5
3.5 3.5
3.0 3.0
4.5 4.5
3.0 3.0
2.0 2.0
3.0 3.0
4.0 4.0
3.5 3.5
3.5 3.5
4.5 4.5
5.0 5.0
4.0 4.0
1.5 1.5
3.0 3.0
4.0 4.0
3.5 3.5
3.5 3.5
3.5 3.5
2.0 2.0
0.5 0.5
1.0 1.0
3.0 3.0
2.5 2.5
3.5 3.5
4.0 4.0
3.0 3.0
4.0 4.0
3.0 3.0
3.0 3.0
3.0 3.0
2.5 2.5
3.5 3.5
3.0 3.0
3.5 3.5
3.0 3.0
3.5 3.5
3.5 3.5
2.0 2.0
2.5 2.5
4.0 4.0
3.5 3.5
3.0 3.0
3.5 3.5
2.5 2.5
2.5 2.5
3.5 3.5
4.0 4.0
4.5 4.5
2.5 2.5
3.0 3.0
3.5 3.5
2.5 2.5
3.5 3.5
1.0 1.0
3.0 3.0
3.5 3.5
3.0 3.0
2.0 2.0
2.5 2.5
3.5 3.5
1.0 1.0
3.0 3.0
2.0 2.0
2.5 2.5
3.0 3.0
3.0 3.0
2.5 2.5
2.5 2.5
3.0 3.0
3.5 3.5
2.0 2.0
3.5 3.5
3.0 3.0
4.0 4.0
3.5 3.5
3.5 3.5
3.0 3.0
3.5 3.5
4.0 4.0
2.0 2.0
3.5 3.5
3.0 3.0
3.0 3.0
3.0 3.0
4.0 4.0
3.0 3.0
2.5 2.5
2.5 2.5
2.5 2.5


KeyboardInterrupt: 

In [42]:
import pandas as pd

c.execute('SELECT ItemID FROM training_table')
movies = []
[movies.append(x[0]) for x in c.fetchall()]

c.execute('SELECT UserID FROM training_table')
users = []
[users.append(x[0]) for x in c.fetchall()]

user_list = []
[user_list.append([x[0], x[1],x[2]]) for x in data2]

pred1_list = []
[pred1_list.append(x[3]) for x in data2]

pred2_list = []
[pred2_list.append(x[4]) for x in data2]

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

In [43]:
movies = sorted(movies)
movies = set(movies)
movies = list(movies)

users = sorted(users)
users = set(users)
users = list(users)
users

[1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 47,
 48,
 49,
 50,
 51,
 52,
 53,
 54,
 55,
 56,
 58,
 59,
 60,
 61,
 62,
 63,
 65,
 66,
 67,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 84,
 85,
 86,
 87,
 89,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 98,
 99,
 100,
 101,
 103,
 104,
 105,
 106,
 107,
 108,
 109,
 110,
 111,
 113,
 114,
 115,
 116,
 117,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 129,
 130,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 139,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 157,
 159,
 160,
 161,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 173,
 174,
 175,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 184,
 185,
 186,
 187,
 188,
 189,
 190,
 191,
 192,

In [96]:
ratings_df = pd.DataFrame(user_list, columns = ["UserID", "MovieID", "Rating"])
ratings_df.head()

UserID  MovieID  Rating
0       1    12793     4.0
1       1      113     1.5
2       1     1876     3.0
3       1    15482     4.5
4       1     2964     3.5

In [32]:
ratings_df

UserID  MovieID  Rating
0             1    12793     4.0
1             1      113     1.5
2             1     1876     3.0
3             1    15482     4.5
4             1     2964     3.5
...         ...      ...     ...
9425740  283229     2916     3.0
9425741  283229    16201     5.0
9425742  283229     6853     5.0
9425743  283229    19353     4.0
9425744  283229    13849     3.0

[9425745 rows x 3 columns]

In [97]:
R_df = ratings_df.to_numpy(index = "UserID", columns="MovieID", values="Rating").fillna(0)
R_df.head()

TypeError: to_numpy() got an unexpected keyword argument 'index'

In [99]:
ratings_df2 = pd.DataFrame(user_list, columns=["UserID","MovieID","Rating"])
R_df = ratings_df2.to_numpy()

In [102]:
print(len(R_df))

9425745


In [ ]:
# Find patterns in training data
# Use patterns to predict with average scores

In [46]:
from sklearn.naive_bayes import GaussianNB

c.execute('SELECT UserID, ItemID FROM training_table')
features = []
[features.append((x[0], x[1])) for x in c.fetchall()]

c.execute('SELECT Rating FROM training_table')
labels = []
[labels.append(x[0]) for x in c.fetchall()]

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

In [51]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(features, labels, test_size=0.33, random_state=42)

In [78]:
from sklearn.linear_model import LinearRegression


In [80]:
model = LinearRegression()
model.fit(X_train, y_train)
y_pred = model.predict(X_test)

In [81]:
from sklearn import metrics
print("Accuracy: ", metrics.accuracy_score(y_test, y_pred))

ValueError: continuous is not supported